In [16]:
import Rk4 
import read_coils as rc
import plotly.graph_objects as go
import matplotlib.pyplot as plt
import numpy as np
import imp
import json
imp.reload(Rk4)

<module 'Rk4' from 'C:\\Users\\Johansell Villalobos\\Estudiantes ITCR\\Team Channel - Top Secret\\Codes\\Johan\\MHD\\mhdequilibrium\\Medusa\\Campo Medusa\\Rk4.py'>

In [2]:
data = rc.read_coil('coils.MEDUSACR')
print(data.shape)

(8,)


In [3]:
def carttotorcil(data):
    x, y, z, *_ = data.T
    
    R = np.sqrt(x**2+y**2)
    R0 = 0.5*(max(R)-min(R))+min(R)
    

    phi = np.arctan2(y,x)

    rtor = np.sqrt((R-R0)**2+z**2)
    theta = np.arctan2(z, (R-R0))+np.pi
    theta, ind = np.unique(theta,return_index=True)
    data = data[ind]
    last = data[0].copy()
    last[3] = 0
    data = np.append(data, [last], axis=0)
    return data


In [14]:
def order_coords(data):
    data_temp = []
    for i in range(len(data)):
        data_temp.append(carttotorcil(data[i]))
    return np.array(data_temp)

ordereddata = order_coords(data)
ordereddata.T[0:3] *= 1e-3

In [5]:
lis = ordereddata.tolist()
with open("coilsmedusaordenadas.txt", "w+") as f:
    f.write(json.dumps(lis))

In [6]:
with open("coilsmedusaordenadas.txt") as f:
    datos=f.read()
    arreglo =np.array(json.loads(datos))

In [7]:
layout = go.Layout(
            scene=dict(
                aspectmode='data'
            ))
fig = go.Figure(layout=layout)

for i in ordereddata: 
    x, y, z, _= i.T
    fig.add_trace(go.Scatter3d(x=x, y=y, z=z, line=dict(width=0)))
    
fig.show()

In [23]:
#integracion de ecuacion de linea de campo 
#ajuste de forma de datos para realizar la integración
init_pos = np.array([0.2,0.000000e+00,0.000000e+00])
linedata, _ = Rk4.RK4(1000, 25000, init_pos, ordereddata)

KeyboardInterrupt: 

In [33]:
import coil_biot as cb
init_pos = np.array([0.08,0.000000e+00,0.000000e+00])
cb.biot(ordereddata, init_pos)

array([-2.49269331e-06,  9.98842185e-02, -9.92359208e-06])

In [18]:
x,y,z, *_ = linedata[0:20000].T

layout = go.Layout(
            scene=dict(
                aspectmode='data'
            ))
fig2 = go.Figure(layout=layout)


fig2.add_trace(go.Scatter3d(x=x, y=y, z=z))
    
fig2.show()
